In [1]:
from matplotlib import pyplot as plt
from matplotlib.image import imread
import pandas as pd
from collections import Counter
import json
import os
import re
import tempfile
import numpy as np
from os.path import exists
from imblearn.under_sampling import RandomUnderSampler
from PIL import ImageFile
import sklearn as sk
from sklearn.model_selection import train_test_split, StratifiedShuffleSplit
import tensorflow as tf
import tensorflow.keras
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Dense, Dropout, Flatten, Activation
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
# custom modules
import image_faults

ImageFile.LOAD_TRUNCATED_IMAGES = True

In [2]:
def add_regularization(model, regularizer=tf.keras.regularizers.l2(0.0001)):

    if not isinstance(regularizer, tf.keras.regularizers.Regularizer):
      print("Regularizer must be a subclass of tf.keras.regularizers.Regularizer")
      return model

    for layer in model.layers:
        for attr in ['kernel_regularizer']:
            if hasattr(layer, attr):
              setattr(layer, attr, regularizer)

    # When we change the layers attributes, the change only happens in the model config file
    model_json = model.to_json()

    # Save the weights before reloading the model.
    tmp_weights_path = os.path.join(tempfile.gettempdir(), 'tmp_weights.h5')
    model.save_weights(tmp_weights_path)

    # load the model from the config
    model = tf.keras.models.model_from_json(model_json)
    
    # Reload the model weights
    model.load_weights(tmp_weights_path, by_name=True)
    return model

In [3]:
# image_faults.faulty_images() # removes faulty images
df = pd.read_csv('expanded_class.csv', index_col=[0], low_memory=False)

In [4]:
def dict_pics_jup():
    '''
    {source:target} dict used to replace source urls with image location as input
    '''
    target_dir = os.getcwd() + os.sep + "training_images"
    with open('temp_pics_source_list.txt') as f:
        temp_pics_source_list = json.load(f)
        
    dict_pics = {}
    for k in temp_pics_source_list:
         patt_1 = re.search(r'[^/]+(?=/\$_|.(\.jpg|\.jpeg|\.png))', k, re.IGNORECASE)
         patt_2 = re.search(r'(\.jpg|\.jpeg|\.png)', k, re.IGNORECASE)
         if patt_1 and patt_2 is not None:
             tag = patt_1.group() + patt_2.group().lower()
             file_name = target_dir + os.sep + tag
             dict_pics.update({k:file_name})
    print("{source:target} dictionary created @ " + target_dir)
    return dict_pics

In [5]:
dict_pics = dict_pics_jup()

with open('women_cat_list.txt') as f:
    women_cats = json.load(f)
with open('men_cat_list.txt') as f:
    men_cats = json.load(f)
    
with open('temp_pics_source_list.txt') as f:
    tempics = json.load(f)
# list of image urls that did not get named properly which will be removed from the dataframe
drop_row_vals = []
for pic in tempics:
    try:
        dict_pics[pic]
    except KeyError:
        drop_row_vals.append(pic)

df['PrimaryCategoryID'] = df['PrimaryCategoryID'].astype(str) # pandas thinks ids are ints
ddf = df[df.PictureURL.isin(drop_row_vals)==False] # remove improperly named image files
df = ddf[ddf.PrimaryCategoryID.isin(men_cats)==False] # removes rows of womens categories

blah = pd.Series(df.PictureURL)
df = df.drop(labels=['PictureURL'], axis=1)

blah = blah.apply(lambda x: dict_pics[x])
df = pd.concat([blah, df],axis=1)
df = df.groupby('PrimaryCategoryID').filter(lambda x: len(x)>25) # removes cat outliers

df=df.sample(frac=1)

{source:target} dictionary created @ /tf/training_images


In [6]:
undersample = RandomUnderSampler(sampling_strategy='auto')
train, y_under = undersample.fit_resample(df, df['PrimaryCategoryID'])
print(Counter(train['PrimaryCategoryID']))

Counter({'11632': 6505, '45333': 6505, '53548': 6505, '53557': 6505, '55793': 6505, '62107': 6505, '95672': 6505})


In [7]:
train, test = train_test_split(train, test_size=0.2, random_state=42)
# stratify=train['PrimaryCategoryID']
# train['PrimaryCategoryID'].value_counts()

In [8]:
datagen = ImageDataGenerator(rescale=1./255., 
                             validation_split=.2,
                             #samplewise_std_normalization=True,
                             #horizontal_flip= True,
                             #vertical_flip= True,
                             #width_shift_range= 0.2,
                             #height_shift_range= 0.2,
                             #rotation_range= 90,
                             preprocessing_function=tf.keras.applications.vgg16.preprocess_input)
train_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)],
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(244,244),
    subset='training'
    )
validation_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)], # is using train right?
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(244,244),
    subset='validation'
    )

Found 29143 validated image filenames belonging to 7 classes.
Found 7285 validated image filenames belonging to 7 classes.


In [9]:
imgs, labels = next(train_generator)

In [10]:
def plotImages(images_arr):
    fig, axes = plt.subplots(1, 10, figsize=(20,20))
    axes = axes.flatten()
    for img, ax in zip( images_arr, axes):
        ax.imshow(img)
        ax.axis('off')
    plt.tight_layout()
    plt.show()

In [11]:
#plotImages(imgs)
#print(labels)

In [12]:
physical_devices = tf.config.list_physical_devices('GPU')
print(len(physical_devices))
tf.config.experimental.set_memory_growth(physical_devices[0], True)

1


In [13]:
base_model = tf.keras.applications.vgg16.VGG16(weights='imagenet')

In [14]:
#model = Sequential()
#for layer in base_model.layers[:-1]:
#    model.add(layer)

In [15]:
# loop through layers, add Dropout after layers 'fc1' and 'fc2'
updated_model = Sequential()
for layer in base_model.layers[:-1]:
    updated_model.add(layer)
    if layer.name in ['fc1', 'fc2']:
        updated_model.add(Dropout(.50))

model = updated_model

for layer in model.layers:
    layer.trainable = True

model.add(Dense(units=7, activation='softmax'))

In [16]:
#model = add_regularization(model)
model.summary()


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 block1_conv1 (Conv2D)       (None, 224, 224, 64)      1792      
                                                                 
 block1_conv2 (Conv2D)       (None, 224, 224, 64)      36928     
                                                                 
 block1_pool (MaxPooling2D)  (None, 112, 112, 64)      0         
                                                                 
 block2_conv1 (Conv2D)       (None, 112, 112, 128)     73856     
                                                                 
 block2_conv2 (Conv2D)       (None, 112, 112, 128)     147584    
                                                                 
 block2_pool (MaxPooling2D)  (None, 56, 56, 128)       0         
                                                                 
 block3_conv1 (Conv2D)       (None, 56, 56, 256)       2

In [17]:
model.compile(optimizer=Adam(learning_rate=.0001), loss='categorical_crossentropy',
              metrics=['accuracy'])

In [ ]:
model.fit(x=train_generator,
          steps_per_epoch=len(train_generator),
          validation_data=validation_generator,
          validation_steps=len(validation_generator),
          epochs=30,
          verbose=1)

Epoch 1/30
911/911 [==============================] - 329s 356ms/step - loss: 1.8477 - accuracy: 0.2577 - val_loss: 1.6306 - val_accuracy: 0.3669
Epoch 2/30
911/911 [==============================] - 322s 353ms/step - loss: 1.4882 - accuracy: 0.4353 - val_loss: 1.4317 - val_accuracy: 0.4784
Epoch 3/30
911/911 [==============================] - 323s 354ms/step - loss: 1.3046 - accuracy: 0.5158 - val_loss: 1.2747 - val_accuracy: 0.5235
Epoch 4/30
911/911 [==============================] - 319s 350ms/step - loss: 1.1691 - accuracy: 0.5681 - val_loss: 1.2090 - val_accuracy: 0.5529
Epoch 5/30
911/911 [==============================] - 317s 348ms/step - loss: 1.0389 - accuracy: 0.6185 - val_loss: 1.1774 - val_accuracy: 0.5682
Epoch 6/30
911/911 [==============================] - 317s 348ms/step - loss: 0.9125 - accuracy: 0.6656 - val_loss: 1.2237 - val_accuracy: 0.5639
Epoch 7/30
147/911 [===>..........................] - ETA: 3:39 - loss: 0.7312 - accuracy: 0.7256